In [4]:
import os
import pickle
import random
import time

import PIL
import numpy as np
import pandas as pd
import tensorflow as tf
from PIL import Image
from tensorflow.keras import Input, Model
from tensorflow.keras import backend as K
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.layers import Dense, LeakyReLU, BatchNormalization, ReLU, Reshape, UpSampling2D, Conv2D, Activation, \
    concatenate, Flatten, Lambda, Concatenate
from tensorflow.keras.optimizers import Adam
from matplotlib import pyplot as plt


import tensorflow as tf
    
with tf.device('/gpu:0'):
    def load_class_ids(class_info_file_path):
        """
        Load class ids from class_info.pickle file
        """
        with open(class_info_file_path, 'rb') as f:
            class_ids = pickle.load(f, encoding='latin1')
            return class_ids


    def load_embeddings(embeddings_file_path):
        """
        훈련된 텍스트 임베딩을 불러옴
        """
        with open(embeddings_file_path, 'rb') as f:
            embeddings = pickle.load(f, encoding='latin1')
            embeddings = np.array(embeddings)
            print('embeddings: ', embeddings.shape)
        return embeddings

    def load_filenames(filenames_file_path):
        """
        Load filenames.pickle file and return a list of all file names
        """
        with open(filenames_file_path, 'rb') as f:
            filenames = pickle.load(f, encoding='latin1')
        return filenames

    def load_bounding_boxes(dataset_dir):
        """
        이미지와 그에 상응하는 바운딩 박스를 짝지어 딕셔너리로 만들어 출력
        """
        # 바운딩 박스 전체 경로
        bounding_boxes_path = os.path.join(dataset_dir, 'list_bbox_celeba_pure.csv')
        file_paths_path = os.path.join(dataset_dir, 'list_filenames.csv')

        # bounding_boxes.txt 와 images.txt 파일을 읽어옴
        df_bounding_boxes = pd.read_csv(bounding_boxes_path, header=None).astype(int)
        df_file_names = pd.read_csv(file_paths_path, header=None)

        # 전체 이미지 파일 명이 순서대로 적힌 리스트를 만듬
        file_names = df_file_names[0].tolist() 

        # 파일 이름에 대응하는 바운딩 박스가 들어갈 딕셔너리를 만듬 (딕셔너리는 크기를 임의로 증가시킬수 있으므로 초기 사이즈는 아무렇게나)
        filename_boundingbox_dict = {}

        # 이미지 파일과 그에 해당하는 바운딩 박스를 딕셔너리로 만듬 (key = 이미지 파일 이름)
        for i in range(0, len(file_names)):
            # Get the bounding box
            bounding_box = df_bounding_boxes.iloc[i][:].tolist()
            key = file_names[i][:-4] + '.jpg'
            filename_boundingbox_dict[key] = bounding_box

        return filename_boundingbox_dict
    '''
    새 이미지가 크롭핑 되어있지 않기 크롭하기 위한 바운딩 박스 좌표 값이 파일에 주어지며,
    그 파일을 토대로 이미지를 크로핑 한 후,
    크로핑된 모든 이미지를 지정한 이미지 크기 (image_size) 값으로 바꾼다
    '''
    def get_img(img_path, bbox, image_size):
        """
        Load and resize image
        """
        img = Image.open(img_path).convert('RGB')
        width, height = img.size
        if bbox is not None:
            R = int(np.maximum(bbox[2], bbox[3]) * 0.75)
            center_x = int((2 * bbox[0] + bbox[2]) / 2)
            center_y = int((2 * bbox[1] + bbox[3]) / 2)
            y1 = np.maximum(0, center_y - R)
            y2 = np.minimum(height, center_y + R)
            x1 = np.maximum(0, center_x - R)
            x2 = np.minimum(width, center_x + R)
            img = img.crop([x1, y1, x2, y2])
        img = img.resize(image_size, PIL.Image.BILINEAR)
        return img


    def load_dataset(filenames_file_path, cub_dataset_dir, embeddings_file_path, image_size):
        """
        Load dataset
        """
        filenames = load_filenames(filenames_file_path)
        '''
        class_ids = load_class_ids(class_info_file_path)
        '''
        bounding_boxes = load_bounding_boxes(cub_dataset_dir)
        all_embeddings = load_embeddings(embeddings_file_path)

        X, y, embeddings = [], [], []

        print("Embeddings shape:", all_embeddings.shape)

        # 각 이미지에 해당하는 바운딩 박스 딕셔너리를 추출하여 get_img 함수로 크로핑되고 같은 크기로 바뀐 이미지를 
        for index, filename in enumerate(filenames):
            bounding_box = bounding_boxes[filename]

            try:
                # Load images
                img_name = '{0}/images/{1}'.format(cub_dataset_dir, filename)
                img = get_img(img_name, bounding_box, image_size)
                '''
                all_embeddings1 = all_embeddings[index, :, :]

                embedding_ix = random.randint(0, all_embeddings1.shape[0] - 1)
                '''
                embedding = all_embeddings[index, :]
                # X = 정제한 이미지 리스트
                X.append(np.array(img))
                '''
                # y = 정제한 이미지 인덱스
                y.append(class_ids[index])
                '''
                # embeddings = 
                embeddings.append(embedding)
            except Exception as e:
                print(e)

        X = np.array(X)
        y = np.array(y)
        embeddings = np.array(embeddings)
        return X, embeddings


    def generate_c(x):
        mean = x[:, :128]
        log_sigma = x[:, 128:]
        stddev = K.exp(log_sigma)
        epsilon = K.random_normal(shape=K.constant((mean.shape[1],), dtype='int32'))
        c = stddev * epsilon + mean
        return c


    def build_ca_model():
        """
        (1024,)의 텍스트 인코더 신경망의 출력을 입력으로 받고 (256,) 의 텐서를 출력
        """
        input_layer = Input(shape=(1024,))
        x = Dense(256)(input_layer)
        x = LeakyReLU(alpha=0.2)(x)
        model = Model(inputs=[input_layer], outputs=[x])
        return model


    def build_embedding_compressor_model():
        """
        입력 속성값 (40,) 을 (128,) 의 벡터로 확장하는 네트워크
        """
        input_layer = Input(shape=(40,))
        x = Dense(128)(input_layer)
        x = ReLU()(x)

        model = Model(inputs=[input_layer], outputs=[x])
        return model


    def build_stage1_generator():
        """
        Stage-I 의 generator 
        *** 이 신경망 안에 CA 신경망과 생성기 신경망이 들어가 있다!!!! ***
        그러므로, 입력으로 텍스트 임베딩 출력 (1024,)과 잡음 변수(100,) 을 받는다
        """
        '''
        input_layer = Input(shape=(1024,))
        x = Dense(256)(input_layer)
        mean_logsigma = LeakyReLU(alpha=0.2)(x)

        c = Lambda(generate_c)(mean_logsigma)

        input_layer2 = Input(shape=(100,))
        gen_input = Concatenate(axis=1)([c, input_layer2])
        '''
        # 텍스트 조건부 변수를 잡음 변수와 접합(concatenation) -> cGAN

        input_layer = Input(shape=(40,))
        x = Dense(128 * 8 * 4 * 4, use_bias=False)(input_layer)
        x = ReLU()(x)

        x = Reshape((4, 4, 128 * 8), input_shape=(128 * 8 * 4 * 4,))(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(512, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(256, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(128, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = UpSampling2D(size=(2, 2))(x)
        x = Conv2D(64, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = ReLU()(x)

        x = Conv2D(3, kernel_size=3, padding="same", strides=1, use_bias=False)(x)
        x = Activation(activation='tanh')(x)

        stage1_gen = Model(inputs=input_layer, outputs=x)
        '''
        stage - I gen 은 입력된 문장의 임베딩을 바탕으로 (+잡음 변수) 이미지를 생성 함 
        '''
        return stage1_gen


    def build_stage1_discriminator():
        """
        Create a model which takes two inputs
        1. One from above network
        2. One from the embedding layer
        3. Concatenate along the axis dimension and feed it to the last module which produces final logits
        """
        input_layer = Input(shape=(64, 64, 3))

        x = Conv2D(64, (4, 4),
                   padding='same', strides=2,
                   input_shape=(64, 64, 3), use_bias=False)(input_layer)
        x = LeakyReLU(alpha=0.2)(x)

        x = Conv2D(128, (4, 4), padding='same', strides=2, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = LeakyReLU(alpha=0.2)(x)

        x = Conv2D(256, (4, 4), padding='same', strides=2, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = LeakyReLU(alpha=0.2)(x)

        x = Conv2D(512, (4, 4), padding='same', strides=2, use_bias=False)(x)
        x = BatchNormalization()(x)
        x = LeakyReLU(alpha=0.2)(x)

        '''
        실제 이미지에 해당하는 압축된 임베딩을 입력
        '''
        input_layer2 = Input(shape=(4, 4, 128))

        '''
        입력 이미지와 압축 텍스트 임베딩을 합침
        '''
        merged_input = concatenate([x, input_layer2])

        x2 = Conv2D(64 * 8, kernel_size=1,
                    padding="same", strides=1)(merged_input)
        x2 = BatchNormalization()(x2)
        x2 = LeakyReLU(alpha=0.2)(x2)
        x2 = Flatten()(x2)
        x2 = Dense(1)(x2)
        x2 = Activation('sigmoid')(x2)

        stage1_dis = Model(inputs=[input_layer, input_layer2], outputs=x2)
        '''
        출력은 입력 이미지가 진짜인지 가짜인지에 관한 확률(sigmoid)을 출력
        '''
        return stage1_dis


    def build_adversarial_model(gen_model, dis_model):
        input_layer = Input(shape=(40,))
        input_layer3 = Input(shape=(4, 4, 128))

        x = gen_model(input_layer)

        dis_model.trainable = False
        valid = dis_model([x, input_layer3])

        model = Model(inputs=[input_layer, input_layer3], outputs=valid)
        return model


    def KL_loss(y_true, y_pred):
        mean = y_pred[:, :128]
        logsigma = y_pred[:, :128]
        loss = -logsigma + .5 * (-1 + K.exp(2. * logsigma) + K.square(mean))
        loss = K.mean(loss)
        return loss


    def custom_generator_loss(y_true, y_pred):
        # Calculate binary cross entropy loss
        return K.binary_crossentropy(y_true, y_pred)


    def save_rgb_img(img, path):
        """
        Save an rgb image
        """
        fig = plt.figure()
        ax = fig.add_subplot(1, 1, 1)
        ax.imshow(img)
        ax.axis("off")
        ax.set_title("Image")

        plt.savefig(path)
        plt.close()


    def write_log(callback, name, loss, batch_no):
        """
        Write training summary to TensorBoard
        """
        with callback.as_default():
              tf.summary.scalar(name, loss, batch_no)
              callback.flush()
 







    '''
    Stage - I stackGAN 훈련
    '''
    if __name__ == '__main__':
        '''
        하이퍼파라미터(불변 파라미터) 지정
        '''
        data_dir = "C:/Users/user/Desktop/CelebA_dataset_reduce"
        train_dir = data_dir + "/train"
        test_dir = data_dir + "/test"
        image_size = 64
        batch_size = 100
        z_dim = 100
        stage1_generator_lr = 0.00008
        stage1_discriminator_lr = 0.00008
        stage1_lr_decay_step = 600
        epochs = 200
        condition_dim = 128

        embeddings_file_path_train = train_dir + "/attr_(embeddings).pickle"
        embeddings_file_path_test = test_dir + "/attr_(embeddings).pickle"

        filenames_file_path_train = train_dir + "/filenames.pickle"
        filenames_file_path_test = test_dir + "/filenames.pickle"

        '''
        class_info_file_path_train = train_dir + "/class_info.pickle"
        class_info_file_path_test = test_dir + "/class_info.pickle"
        '''

        cub_dataset_dir = data_dir + "/img_align_celeba"

        '''
        optimizer 정의
        '''
        dis_optimizer = Adam(lr=stage1_discriminator_lr, beta_1=0.5, beta_2=0.999)
        gen_optimizer = Adam(lr=stage1_generator_lr, beta_1=0.5, beta_2=0.999)

        """"
        dataset 로드하기
        """
        X_train, embeddings_train = load_dataset(filenames_file_path=filenames_file_path_train,
                                                          cub_dataset_dir=cub_dataset_dir,
                                                          embeddings_file_path=embeddings_file_path_train,
                                                          image_size=(64, 64))

        X_test, embeddings_test = load_dataset(filenames_file_path=filenames_file_path_test,
                                                       cub_dataset_dir=cub_dataset_dir,
                                                       embeddings_file_path=embeddings_file_path_test,
                                                       image_size=(64, 64))


embeddings:  (16000, 40)
Embeddings shape: (16000, 40)
embeddings:  (4000, 40)
Embeddings shape: (4000, 40)


In [5]:
with tf.device('/gpu:0'):
        """
        신경망 빌드 & compile
        """
        '''
        ca_model = build_ca_model()
        ca_model.compile(loss="binary_crossentropy", optimizer="adam")
        '''
        stage1_dis = build_stage1_discriminator()
        stage1_dis.compile(loss='binary_crossentropy', optimizer=dis_optimizer)

        stage1_gen = build_stage1_generator()
        stage1_gen.compile(loss="mse", optimizer=gen_optimizer)

        embedding_compressor_model = build_embedding_compressor_model()
        embedding_compressor_model.compile(loss="binary_crossentropy", optimizer="adam")

        '''
        stage-I GAN 빌드& 컴파일
        이때, stage-I 의 discriminator 는 훈련시키지 않고 stage-I generator 의 가중치만 업데이트
        '''
        adversarial_model = build_adversarial_model(gen_model=stage1_gen, dis_model=stage1_dis)
        adversarial_model.compile(loss=['binary_crossentropy', KL_loss], loss_weights=[1, 2.0],
                                  optimizer=gen_optimizer, metrics=None)

        """
        tensorboard.set_model(stage1_gen)
        tensorboard.set_model(stage1_dis)
        '''
        tensorboard.set_model(ca_model)
        '''
        tensorboard.set_model(embedding_compressor_model)
        """
        # Generate an array containing real and fake values
        # Apply label smoothing as well
        real_labels = np.ones((batch_size, 1), dtype=float) * 0.9
        fake_labels = np.zeros((batch_size, 1), dtype=float) * 0.1
        '''
        매 epoch 마다 아래를 반복함
        '''
        for epoch in range(epochs):
            print("========================================")
            print("Epoch is:", epoch)
            print("Number of batches", int(X_train.shape[0] / batch_size))

            gen_losses = []
            dis_losses = []

            # Load data and train model
            number_of_batches = int(X_train.shape[0] / batch_size)
            for index in range(number_of_batches):
                print("Batch:{}".format(index+1))
                '''
                모델에 입력으로 들어갈 이미지와 텍스트 임베딩을 받아옴 (각 텍스트 임베딩은 각 이미지에 대응 됨)
                '''
                # 원래는 CA 의 출력이 stage-I 으로 들어가야 하지만 gen 안에 CA 가 있음
                z_noise = np.random.normal(0, 1, size=(batch_size, z_dim))
                # 배치 사이즈만큼 훈련(실제) 이미지를 추출
                image_batch = X_train[index * batch_size:(index + 1) * batch_size]
                # 추출한 이미지에 대응하는 임베딩을 추출
                embedding_batch = embeddings_train[index * batch_size:(index + 1) * batch_size]
                # 이미지들을 정규화하여 값을 작게 만듬
                image_batch = (image_batch - 127.5) / 127.5

                # stage-I 의 gen 에서 텍스트 임베딩을 바탕으로 저 해상도 fake 이미지를 생성
                # 이때, 두 stage 는 랜덤하게 생성한 텍스트 임베딩을 나머지 입력으로 받음
                fake_images = stage1_gen.predict(embedding_batch, verbose=3)

                # stage-I dis 에 들어갈 압축 텍스트 임베딩을 랜덤하게 생성한 텍스트 임베딩 기반으로 생성
                compressed_embedding = embedding_compressor_model.predict_on_batch(embedding_batch)
                compressed_embedding = np.reshape(compressed_embedding, (-1, 1, 1, condition_dim))
                compressed_embedding = np.tile(compressed_embedding, (1, 4, 4, 1))
                '''
                discriminator 에서 입력 이미지가 CNN 을 통과한 결과와 속성값 (40,) 을 concatenate 해 주기 위해서는,
                속성값 (40,) 를 compressor 네트워크를 통해 (128,) 로 확장하고,
                reshape, tile 함수를 이용해 CNN 결과 (4, 4, 512) 와 (4, 4, :) 부분을 맞추어 주어야 한다.
                '''
                
                """
                stage-I dis 를 훈련함
                """
                # 실제 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 1 (이미지가 진짜라는 의미) 로 하여,
                # dis 가 실제 이미지를 잘 분류 하게끔 훈련
                dis_loss_real = stage1_dis.train_on_batch([image_batch, compressed_embedding],
                                                          np.reshape(real_labels, (batch_size, 1)))
                # gen 이 생성한 가짜 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 0 (이미지가 가짜라는 의미) 로 하여,
                # dis 가 가짜 이미지를 잘 분류 하게끔 훈련
                dis_loss_fake = stage1_dis.train_on_batch([fake_images, compressed_embedding],
                                                          np.reshape(fake_labels, (batch_size, 1)))
                # 실제 이미지와 압축 텍스트 임베딩을 입력으로 하고 모든 레이블을 0 (이미지가 가짜라는 의미) 로 하여,
                # dis 가 실제 이미지를 잘 분류 하게끔 훈련
                dis_loss_wrong = stage1_dis.train_on_batch([image_batch[:(batch_size - 1)], compressed_embedding[1:]],
                                                           np.reshape(fake_labels[1:], (batch_size-1, 1)))

                d_loss = 0.5 * np.add(dis_loss_real, 0.5 * np.add(dis_loss_wrong, dis_loss_fake))

                print("d_loss_real:{}".format(dis_loss_real))
                print("d_loss_fake:{}".format(dis_loss_fake))
                print("d_loss_wrong:{}".format(dis_loss_wrong))
                print("d_loss:{}".format(d_loss))

                """
                stage-I GAN 을 훈련함
                이때, stage-I 의 discriminator 는 훈련시키지 않고 stage-I generator 의 가중치만 업데이트
                """
                g_loss = adversarial_model.train_on_batch([embedding_batch, compressed_embedding],[K.ones((batch_size, 1)) * 0.9, K.ones((batch_size, 256)) * 0.9])
                print("g_loss:{}".format(g_loss))

                dis_losses.append(d_loss)
                gen_losses.append(g_loss)

            """
            각 epoch 마다 Tensorboard 에 loss 저장
            """
            writer = tf.summary.create_file_writer("logs/".format(time.time()))
            write_log(writer, 'discriminator_loss', np.mean(dis_losses), epoch)
            write_log(writer, 'generator_loss', np.mean(gen_losses[0]), epoch)
            '''
            tf.summary.scalar('discriminator_loss', np.mean(dis_losses), epoch)
            tf.summary.scalar('generator_loss', np.mean(gen_losses[0]), epoch)
            
            tf.summary.scalar('discriminator_loss', np.mean(dis_losses))
            tf.summary.scalar('generator_loss', np.mean(gen_losses[0]))
            summary_op = tf.summary.merge()
            summary_writer = tf.summary.FileWriter("logs/".format(time.time()))
            '''    
            # 매 두번의 epoch 마다 이미지 gen & 이미지 저장
            if epoch % 2 == 0:
                # z_noise2 = np.random.uniform(-1, 1, size=(batch_size, z_dim))
                z_noise2 = np.random.normal(0, 1, size=(batch_size, z_dim))
                embedding_batch = embeddings_test[0:batch_size]
                fake_images = stage1_gen.predict_on_batch(embedding_batch)

                # Save images
                for i, img in enumerate(fake_images[:10]):
                    save_rgb_img(img, "results/gen_{}_{}.png".format(epoch, i))
                    
            if epoch % 50 == 0:
                # Save models
                stage1_gen.save_weights("weights/stage1_gen_epoch_{0}.h5".format(epochs))
                stage1_dis.save_weights("weights/stage1_dis_epoch_{0}.h5".format(epochs))

        '''
        이제 훈련된 stage-I 의 generator 와 discriminator 을 얻음 (+ embedding_compressor) 
        '''

Epoch is: 0
Number of batches 160
Batch:1
d_loss_real:0.7236115336418152
d_loss_fake:1.6515235900878906
d_loss_wrong:3.2633330821990967
d_loss:1.5905199348926544
g_loss:0.7146225571632385
Batch:2
d_loss_real:0.5836983323097229
d_loss_fake:0.4909856915473938
d_loss_wrong:0.6535986661911011
d_loss:0.5779952555894852
g_loss:0.7303970456123352
Batch:3
d_loss_real:1.6868505477905273
d_loss_fake:0.17465265095233917
d_loss_wrong:0.7586811184883118
d_loss:1.0767587162554264
g_loss:0.7068268656730652
Batch:4
d_loss_real:1.7669199705123901
d_loss_fake:0.31950080394744873
d_loss_wrong:0.6933157444000244
d_loss:1.1366641223430634
g_loss:0.718536376953125
Batch:5
d_loss_real:1.4764457941055298
d_loss_fake:0.08788745850324631
d_loss_wrong:1.1104680299758911
d_loss:1.0378117691725492
g_loss:0.6970932483673096
Batch:6
d_loss_real:1.397120714187622
d_loss_fake:0.27892932295799255
d_loss_wrong:0.7619447708129883
d_loss:0.9587788805365562
g_loss:0.6987936496734619
Batch:7
d_loss_real:1.3453383445739746
d

g_loss:0.3293558359146118
Batch:53
d_loss_real:1.0092179775238037
d_loss_fake:0.001391058904118836
d_loss_wrong:0.7629265189170837
d_loss:0.6956883832172025
g_loss:0.3261401057243347
Batch:54
d_loss_real:0.9879654049873352
d_loss_fake:0.0017335647717118263
d_loss_wrong:0.8104386925697327
d_loss:0.6970257668290287
g_loss:0.3257136940956116
Batch:55
d_loss_real:0.9461456537246704
d_loss_fake:0.001653863349929452
d_loss_wrong:0.7664095759391785
d_loss:0.6650886866846122
g_loss:0.3259034752845764
Batch:56
d_loss_real:0.9456022381782532
d_loss_fake:0.0020591644570231438
d_loss_wrong:0.7965101599693298
d_loss:0.6724434501957148
g_loss:0.32663699984550476
Batch:57
d_loss_real:0.9494954943656921
d_loss_fake:0.0010782461613416672
d_loss_wrong:0.7720988988876343
d_loss:0.66804203344509
g_loss:0.3287767171859741
Batch:58
d_loss_real:0.9632890820503235
d_loss_fake:0.0017821494257077575
d_loss_wrong:0.7575880885124207
d_loss:0.6714871005096938
g_loss:0.3283064365386963
Batch:59
d_loss_real:0.966304

g_loss:0.3256838917732239
Batch:105
d_loss_real:0.8883340954780579
d_loss_fake:0.0010826836805790663
d_loss_wrong:0.7046266794204712
d_loss:0.6205943885142915
g_loss:0.32668906450271606
Batch:106
d_loss_real:0.8690627813339233
d_loss_fake:0.0007514633471146226
d_loss_wrong:0.7376513481140137
d_loss:0.6191320935322437
g_loss:0.3278934061527252
Batch:107
d_loss_real:0.8943895697593689
d_loss_fake:0.0008925510919652879
d_loss_wrong:0.6912763118743896
d_loss:0.6202370006212732
g_loss:0.32602640986442566
Batch:108
d_loss_real:0.8934074640274048
d_loss_fake:0.0007358173024840653
d_loss_wrong:0.6912847757339478
d_loss:0.6197088802728103
g_loss:0.3255913257598877
Batch:109
d_loss_real:0.9157518744468689
d_loss_fake:0.0008228703518398106
d_loss_wrong:0.700783371925354
d_loss:0.6332774977927329
g_loss:0.3264918923377991
Batch:110
d_loss_real:0.8445001244544983
d_loss_fake:0.0008567834156565368
d_loss_wrong:0.7366685271263123
d_loss:0.6066313898627413
g_loss:0.32619014382362366
Batch:111
d_loss_r

g_loss:0.3272782862186432
Batch:157
d_loss_real:0.8642919063568115
d_loss_fake:0.0006883343448862433
d_loss_wrong:0.6727160215377808
d_loss:0.6004970421490725
g_loss:0.3254552185535431
Batch:158
d_loss_real:0.8679051995277405
d_loss_fake:0.0007229697075672448
d_loss_wrong:0.6732782125473022
d_loss:0.6024528953275876
g_loss:0.32702457904815674
Batch:159
d_loss_real:0.836692750453949
d_loss_fake:0.0007518077618442476
d_loss_wrong:0.688640296459198
d_loss:0.590694401282235
g_loss:0.3255157768726349
Batch:160
d_loss_real:0.8417830467224121
d_loss_fake:0.0006972161936573684
d_loss_wrong:0.6954367756843567
d_loss:0.5949250213307096
g_loss:0.3268811106681824


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping i

...

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


Epoch is: 199
Number of batches 160
Batch:1
d_loss_real:0.32538849115371704
d_loss_fake:9.411232895217836e-07
d_loss_wrong:0.0004105805710423738
d_loss:0.1627971260004415
g_loss:0.32516998052597046
Batch:2
d_loss_real:0.32899609208106995
d_loss_fake:7.594185262860265e-07
d_loss_wrong:0.0015021342551335692
d_loss:0.16487376945894994
g_loss:0.3252444863319397
Batch:3
d_loss_real:0.3290519714355469
d_loss_fake:1.0361635531808133e-06
d_loss_wrong:0.0034998946357518435
d_loss:0.1654012184175997
g_loss:0.32519614696502686
Batch:4
d_loss_real:0.3269476592540741
d_loss_fake:5.621296281788091e-07
d_loss_wrong:0.0018708191346377134
d_loss:0.16394167494310352
g_loss:0.3256584405899048
Batch:5
d_loss_real:0.32747721672058105
d_loss_fake:6.445258122766973e-07
d_loss_wrong:0.0003147631650790572
d_loss:0.16381746028301336
g_loss:0.3251696527004242
Batch:6
d_loss_real:0.3255961239337921
d_loss_fake:4.7276549253183475e-07
d_loss_wrong:0.0001680494606262073
d_loss:0.16284019252342574
g_loss:0.3251587748

d_loss_real:0.3268781006336212
d_loss_fake:7.632563665538328e-07
d_loss_wrong:0.0005276307929307222
d_loss:0.16357114882913493
g_loss:0.3252403736114502
Batch:52
d_loss_real:0.32948121428489685
d_loss_fake:4.1419073681936425e-07
d_loss_wrong:0.000783358933404088
d_loss:0.16493655042348365
g_loss:0.325313001871109
Batch:53
d_loss_real:0.3259861469268799
d_loss_fake:3.7154958931751025e-07
d_loss_wrong:0.000799920002464205
d_loss:0.16319314635145332
g_loss:0.32559430599212646
Batch:54
d_loss_real:0.34252625703811646
d_loss_fake:4.5332311060519714e-07
d_loss_wrong:0.0023474819026887417
d_loss:0.17185011232550806
g_loss:0.3276353180408478
Batch:55
d_loss_real:0.32935580611228943
d_loss_fake:7.303860911633819e-07
d_loss_wrong:0.0005321374628692865
d_loss:0.16481112001838483
g_loss:0.32530978322029114
Batch:56
d_loss_real:0.32703399658203125
d_loss_fake:5.215505893829686e-07
d_loss_wrong:0.0009552741539664567
d_loss:0.16375594721715458
g_loss:0.32537901401519775
Batch:57
d_loss_real:0.3261541

g_loss:0.3256063163280487
Batch:102
d_loss_real:0.3279249966144562
d_loss_fake:4.661162904540106e-07
d_loss_wrong:0.0010232736822217703
d_loss:0.16421843325685614
g_loss:0.3253887891769409
Batch:103
d_loss_real:0.3299826383590698
d_loss_fake:4.234004506997735e-07
d_loss_wrong:0.0008607491035945714
d_loss:0.16520661230554623
g_loss:0.32544079422950745
Batch:104
d_loss_real:0.3422822952270508
d_loss_fake:9.659154329710873e-07
d_loss_wrong:0.0005409701261669397
d_loss:0.17127663162392537
g_loss:0.32769644260406494
Batch:105
d_loss_real:0.35069039463996887
d_loss_fake:6.147166118353198e-07
d_loss_wrong:9.294071787735447e-05
d_loss:0.17536858617860673
g_loss:0.3252696990966797
Batch:106
d_loss_real:0.32758572697639465
d_loss_fake:3.402226411708398e-07
d_loss_wrong:0.0001328815269516781
d_loss:0.16382616892559554
g_loss:0.3256371319293976
Batch:107
d_loss_real:0.32874810695648193
d_loss_fake:5.961671263321477e-07
d_loss_wrong:0.0018145102076232433
d_loss:0.16482783007192836
g_loss:0.32529464

d_loss_real:0.3266977071762085
d_loss_fake:6.465116939580184e-07
d_loss_wrong:0.001297108712606132
d_loss:0.16367329239417927
g_loss:0.32526740431785583
Batch:153
d_loss_real:0.32856518030166626
d_loss_fake:7.202333449640719e-07
d_loss_wrong:0.0010643255664035678
d_loss:0.16454885160077026
g_loss:0.32599982619285583
Batch:154
d_loss_real:0.3280411660671234
d_loss_fake:8.193422331714828e-07
d_loss_wrong:0.003300831187516451
d_loss:0.1648459956659991
g_loss:0.3251645267009735
Batch:155
d_loss_real:0.3281605541706085
d_loss_fake:5.085124143988651e-07
d_loss_wrong:0.0008145020110532641
d_loss:0.16428402971617118
g_loss:0.32585498690605164
Batch:156
d_loss_real:0.3254210352897644
d_loss_fake:6.992787007220613e-07
d_loss_wrong:0.002047477290034294
d_loss:0.16322256178706596
g_loss:0.3258916735649109
Batch:157
d_loss_real:0.32628944516181946
d_loss_fake:5.076884690424777e-07
d_loss_wrong:0.00021010330237913877
d_loss:0.16319737532862177
g_loss:0.3253107964992523
Batch:158
d_loss_real:0.337828